In [ ]:
!pip3 install valohai-cli

In [ ]:
# Account for valohai.com
username = 'foo@bar.com'
password = 'fakepass'
currentProject = '' # leave this empty!

!vh login --username {username} --password {password} --yes

In [ ]:
# Settings for Valohai execution
project = 'testproject'
docker = 'python:3.6'

# Create local project folder
!mkdir -p ~/{project}
%cd ~/{project}

In [ ]:
# Create new Valohai project or link to existing
%cd ~/{project}
if currentProject != project:
    !vh project create -n {project} --yes
    currentProject = project
else:
    !vh project link {project} --yes

In [ ]:
from IPython.core.magic import Magics, magics_class, cell_magic
import os

@magics_class
class ValohaiMagics(Magics):
    @cell_magic
    def valohai(self, line='', cell=None):
        path = os.path.expanduser('~/%s/execute.py' % project)
        
        with open(path, 'w+') as f:
            f.write(cell)
        
        path = os.path.expanduser('~/%s/valohai.yaml' % project)
        with open(path, 'w+') as f:
            f.write('- step:\r\n')
            f.write('    name: jupyter_execution\r\n')
            f.write('    image: %s\r\n' % docker)
            f.write('    command: python execute.py\r\n')
       
        print('Starting execution in Valohai...')
        !vh execution run --adhoc jupyter_execution
        !vh execution logs --stream latest
 
ip = get_ipython()
ip.register_magics(ValohaiMagics)

In [ ]:
%%valohai

a=1
b=2
print("Result", a+b)